# Holiday Reports Created by: Faiza Esmail Updated: 04/01/2024 
This script will create Holiday Reports per country in an excel file. This is a pivot table based on Employees in each country against the type of leave - Holidays,Sick days, Unpaid leave and ad hoc leave. 

In [15]:
# !pip install -r requirements.txt

In [16]:
!pip install pandas==2.0.3

In [17]:
import pandas as pd
import os

from datetime import datetime
from openpyxl.styles import PatternFill, Alignment
from openpyxl.styles import Border, Side
from openpyxl.styles import Font

In [18]:
def style_sheet(ws, row_counter, columns):
    # Make a grey border
    colored_border = Border(
        left=Side(style="thin", color="cecfd3"),
        right=Side(style="thin", color="cecfd3"),
        top=Side(style="thin", color="cecfd3"),
        bottom=Side(style="thin", color="cecfd3"),
    )

    # Make a black border at the bottom only
    thick_black_border = Border(
        bottom=Side(style="thick", color="000000"),
    )

    # Iterating over the sheet from row 5 to end of sheet and to column 6 to set the border
    for row in ws.iter_rows(min_row=5, max_row=row_counter, max_col=6):
        for cell in row:
            cell.border = colored_border

    # Merge cells / set alignment / borders / background color
    n = len(columns) # get the number of column
    # columns[3] is D because columns = [A, C, C, D, E, F]
    ws.merge_cells(f"{columns[3]}3:{columns[-1]}3")
    yellow_fill = PatternFill(
        start_color="fec000", end_color="fec000", fill_type="solid"
    )
    for cells in ws[f"{columns[3]}3:{columns[-1]}3"]:
        for cell in cells:
            cell.fill = yellow_fill
            cell.border = colored_border
            cell.alignment = Alignment(horizontal="center", vertical="center")

    # Adjust column widths to fit the data well
    max_lengths = {
        column: max(len(str(cell.value)) for cell in ws[column]) for column in columns
    }
    for col, length in max_lengths.items():
        ws.column_dimensions[col].width = length + 2

    # Make a dark grey color
    dark_grey_fill = PatternFill(
        start_color="d8dee7", end_color="d8dee7", fill_type="solid"
    )

    # Set background color and border
    for cell in [ws["A3"], ws["B3"], ws["C3"]]:
        cell.fill = dark_grey_fill
        cell.border = colored_border

    # Set background color and border,  putting a black border at the bottom
    for cell in [ws["A4"], ws["B4"], ws["C4"]]:
        cell.fill = dark_grey_fill
        cell.border = colored_border
        cell.border = thick_black_border

    # Make a blue color / white color
    dark_blue_fill = PatternFill(
        start_color="667ba1", end_color="667ba1", fill_type="solid"
    )
    white_font = Font(color="FFFFFF")

    # Set color / text color / border
    wss = [ws[f"{columns[i]}4"] for i in range(3, n)]
    for cell in wss:
        cell.fill = dark_blue_fill
        cell.font = white_font
        cell.border = colored_border
        cell.border = thick_black_border

    # Make light grey color
    light_grey = PatternFill(
        start_color="f2f3f7", end_color="f2f3f7", fill_type="solid"
    )
    # Iterating over data to give it the light grey color
    for row in ws.iter_rows(min_row=5, max_row=row_counter, max_col=3):
        for cell in row:
            cell.fill = light_grey

    # Color cells and putting black border at the bottom
    bottoms = [ws[f"{columns[idx]}{row_counter}"] for idx in range(1, n)]
    for cell in bottoms:
        cell.fill = dark_grey_fill
        cell.border = thick_black_border

    ws[f"A{row_counter}"].border = thick_black_border
    ws.row_dimensions[row_counter].height = 25

In [19]:
def format_date(date):
    return date.strftime("%d/%m/%Y")

In [20]:
def main():
    # Read the excel using pandas
    df = pd.read_excel("AugustHoliday.xlsx")

    # Getting only needed columns from csv
    df = df.loc[
        :,
        [
            "Employee name",
            "Status",
            "Country",
            "Leave date",
            "Type of leave",
            "Duration in days",
        ],
    ]
    
     # Get types of leave
    types = list(df['Type of leave'].unique())

    # Getting approved data only
    df = df[df["Status"] == "approved"]

    # Getting all countries
    countries = df["Country"].unique()

    # Get the current month and year
    current_month = datetime.now().strftime("%b")
    current_year = datetime.now().strftime("%Y")

    df["Leave date"] = pd.to_datetime(df["Leave date"], format='mixed', dayfirst=True)
    # latest_date = df["Leave date"].max()
    # latest_month = str(latest_date.strftime("%b")).upper()
    # latest_year = latest_date.strftime("%Y")

    # Making a folder called "Holiday Report" if one didnt exist
    if not os.path.exists("Holiday Report"):
        os.makedirs("Holiday Report")

    # Looping through all countries
    for country in countries:
        # Getting data of the same country
        df_country = df[df["Country"] == country]

        # Starting an excel file and naming it (Openpxyl is the library)
        #Change the DATE n the NAme of the file
        file_name = f"{country} Holiday Report {current_month}-{current_year}"
        writer = pd.ExcelWriter(f"./Holiday Report/{file_name}.xlsx", engine="openpyxl")

        # Create a new worksheet
        ws = writer.book.create_sheet(title=country)

        # Write the COUNTRY label and actual country name
        ws["A1"] = "COUNTRY"
        ws["B1"] = country

        # Write headers
        ws["A4"] = "Employee name"
        ws["B4"] = "Status"
        ws["C4"] = "Leave date"
        
        # Get column automatically that includes types of leave and Grand Total
        start_ord = ord("C")
        columns = [chr(start_ord + (i + 1)) for i in range(len(types) + 1)]
        for i, t in enumerate(types):
            ws[f"{columns[i]}4"] = t
            
        # Get column for Grand Total
        ws[f"{columns[-1]}4"] = "Grand Total"

        # Row counter is from as we will start writing our data from row 5
        row_counter = 5

        # Iterate over unique employees
        for employee in df_country["Employee name"].unique():
            df_employee = df_country[df_country["Employee name"] == employee]

            # Write employee name and status once
            ws[f"A{row_counter}"] = employee
            ws[f"B{row_counter}"] = "approved"

            # Iterate over the rows of the same employee and writing the data
            for _, row in df_employee.iterrows():
                # format_date changes the date format from 23/12/23 to 23/12/2023
                ws[f"C{row_counter}"] = format_date(row["Leave date"])

                # Writing Duration of days
                idx = types.index(row["Type of leave"])
                if row["Type of leave"] == types[idx]:
                    ws[f"{columns[idx]}{row_counter}"] = row["Duration in days"]
                    ws[f"{columns[-1]}{row_counter}"] = row["Duration in days"]
                else:
                    # In case of empty cells, default to 0 for grand total
                    ws[f"{columns[-1]}{row_counter}"] = 0
                # Increasing the row by one
                row_counter += 1

        # After iterating over all rows, write the totals
        ws[f"B{row_counter}"] = "Approved Total"
        for c in columns[:-1]:
            ws[f"{c}{row_counter}"] = f"=SUM({c}5:{c}{row_counter-1})"
        ws[f"{columns[-1]}{row_counter}"] = ws["B3"] = f"=SUM({columns[-1]}5:{columns[-1]}{row_counter-1})"

        # Write sum of days
        ws["A3"] = "Sum of Duration in days"
        ws["D3"] = f"Jan 2025 - {current_month} 2025"

        # This is a function to all the styling done in the excel sheet
        full_columns = ['A', 'B', 'C'] + columns
        style_sheet(ws, row_counter, full_columns)
       
        writer._save()

    print("FINISHED GENERATING EXCEL FILES")

In [21]:
# Running the main() function to run the program
if __name__ == "__main__":
    main()

FINISHED GENERATING EXCEL FILES
